# Preparação

In [1]:
import pandas as pd
import numpy as np

In [2]:
#Realiza a leitura do dataset utilizado e apresenta as primeiras linhas
dataset = pd.read_csv('Insira aqui o caminho do dataset')
dataset.head()

Date    Year        Type         Country  \
0            2017-06-11  2017.0  Unprovoked       AUSTRALIA   
1            2017-06-10  2017.0  Unprovoked       AUSTRALIA   
2            2017-06-10  2017.0  Unprovoked             USA   
3  Reported 07-Jun-2017  2017.0  Unprovoked  UNITED KINGDOM   
4            2017-06-04  2017.0  Unprovoked             USA   

                Area                                         Location  \
0  Western Australia                         Point Casuarina, Bunbury   
1           Victoria                    Flinders, Mornington Penisula   
2            Florida                      Ponce Inlet, Volusia County   
3        South Devon                                    Bantham Beach   
4            Florida  Middle Sambo Reef off Boca Chica, Monroe County   

        Activity Sex   Age                                             Injury  \
0  Body boarding    M   48                            No injury, board bitten   
1        Surfing    F  NaN                        No injury, knocke off board   
2        Surfing    M   19                            Laceration to left foot   
3       Surfing     M   30  Bruise to leg, cuts to hand sustained when he ...   
4   Spearfishing    M  NaN                                 Laceration to shin   

  Fatal (Y/N)   Time                           Species   Cod_Ataque  
0           N  08h30                   White shark, 4 m           0  
1           N  15h45                       7 gill shark           1  
2           N  10h00                                NaN           2  
3           N    NaN  3m shark, probably a smooth hound           3  
4           N    NaN                           8' shark           4

# Country

In [3]:
#Coluna 'Country'

paises = dataset['Country'].value_counts().to_frame().reset_index().sort_values(by='index', ascending = True)
#Conta a ocorrência de cada país, converte em um dataframe, e organiza o index para melhor visualização
paises.rename(columns = {'index':'pais', 'Country':'ataques'}, inplace = True)
#Renomeia as colunas para termos mais adequados
paises.reset_index(drop = True, inplace = True)
#Realiza um novo reset do index, desta vez sem transformar o antigo em uma coluna
paises

pais  ataques
0          PHILIPPINES        1
1                TONGA        3
2    ADMIRALTY ISLANDS        1
3              ALGERIA        1
4       AMERICAN SAMOA        3
..                 ...      ...
199          VENEZUELA       11
200            VIETNAM       14
201      WESTERN SAMOA        1
202              YEMEN        2
203             YEMEN         7

[204 rows x 2 columns]

In [4]:
#Alguma coisa na escrita de Philippines e Tonga está errada, já que em ordem alfabética deveriam estar mais para o fim da lista
#O Yemen também aparece duas vezes ao fim da lista. Provavelmente há espaços no começo e final dos nomes dos países.
#Vamos remover espaços e organizar o dataframe novamente

for i in range(len(dataset)): #Varre todos os países do dataframe
    pais = dataset.iloc[i,3]
    if  str(pais)[0] == ' ': #Valida se o país começa com um espaço
        dataset.iloc[i,3] = str(pais)[1:] #Remove o espaço inicial
    elif str(pais)[-1] == ' ': #Valida se o país termina com um espaço
        dataset.iloc[i,3] = str(pais)[:-1]


paises = dataset['Country'].value_counts().to_frame().reset_index().sort_values(by='index', ascending = True)
#Conta a ocorrência de cada país, converte em um dataframe, e organiza o index para melhor visualização
paises.rename(columns = {'index':'pais', 'Country':'ataques'}, inplace = True)
#Renomeia as colunas para termos mais adequados
paises.reset_index(drop = True, inplace = True)
#Realiza um novo reset do index, desta vez sem transformar o antigo em uma coluna
paises

pais  ataques
0             ADMIRALTY ISLANDS        1
1                       ALGERIA        1
2                AMERICAN SAMOA        3
3    ANDAMAN / NICOBAR ISLANDAS        1
4                        ANGOLA        1
..                          ...      ...
191                     VANUATU       14
192                   VENEZUELA       11
193                     VIETNAM       14
194               WESTERN SAMOA        1
195                       YEMEN        9

[196 rows x 2 columns]

In [5]:
#Já conseguimos revover 8 divergências na coluna. Agora vamos apenas explorar em grupos de 50 países 
#para verificar se há repetição, já que são relativamente poucos e a tarefa é relativamente rápida

paises['pais'][149:]

149                                  SENEGAL
150                               SEYCHELLES
151                             SIERRA LEONE
152                            SIERRA LEONE?
153                                SINGAPORE
154                                 SLOVENIA
155                          SOLOMON ISLANDS
156                SOLOMON ISLANDS / VANUATU
157                                  SOMALIA
158                             SOUTH AFRICA
159                     SOUTH ATLANTIC OCEAN
160                          SOUTH CHINA SEA
161                              SOUTH KOREA
162                      SOUTH PACIFIC OCEAN
163                  SOUTHWEST PACIFIC OCEAN
164                                    SPAIN
165                                SRI LANKA
166    ST HELENA, British overseas territory
167                              ST. MAARTIN
168                               ST. MARTIN
169                                    SUDAN
170                                   SUDAN?
171       

In [6]:
#As inconsistências encontradas estão listadas abaixo:

# 1)'ASIA?'
# 2)'Between PORTUGAL & INDIA'
# 3)'EGYPT / ISRAEL'
# 4)'EQUATORIAL GUINEA / CAMEROON'
# 5)'England' é diferente de 'ENGLAND'
# 6)'Fiji' é diferente de 'FIJI'
# 7)'INDIAN OCEAN?' é diferente de 'INDIAN OCEAN'
# 8)'IRAN / IRAQ'
# 9)'ITALY / CROATIA'
# 10)'RED SEA?' é diferente de 'RED SEA'
# 11)'RED SEA / INDIAN OCEAN'
# 12)'SIERRA LEONE?' é diferente de 'SIERRA LEONE'
# 13)'SOLOMON ISLANDS / VANUATU'
# 14)'ST MAARTIN' é diferente de 'ST MARTIN'
# 15)'SUDAN?' é diferente de 'SUDAN''
# 16)'UNITED ARAB EMIRATES' é diferente de 'UNITED ARAB EMIRATES (UAE)'
# 17) Podemos unificar ENGLAND e UNITED KINGDOM?

#Com exceção dos itens 5), 6), 14) e 16), que são formas distintas de escrita apenas, vamos incluir o retante em uma lista
#de países cujos locais de ataque sejam duvidosos

lista_duvidas = ['ASIA?', 'Between PORTUGAL & INDIA', 'EQUATORIAL GUINEA / CAMEROON', 'INDIAN OCEAN?', 'IRAN / IRAQ',
                'ITALY / CROATIA','RED SEA?','RED SEA / INDIAN OCEAN', 'SIERRA LEONE?', 'SOLOMON ISLANDS / VANUATU',
                'SUDAN?']

#Para mantermos a informação de dúvida nos dados após a padronização, incluiremos uma nova coluna, chamada 'conf_pais', que 
#conterá valores de 'Sim' (quando o local do ataque for conhecido com certeza) ou 'Não' (caso haja dúvida sobre o local do 
#ataque)

dataset['conf_pais'] = dataset['Country'].apply(lambda pais: "Não" if pais in lista_duvidas else "Sim")

In [7]:
#Após isso, vamos definir o local de ataque como sendo o país que tiver mais ataques dentre os dois candidatos
#Por exemplo:
paises[(paises['pais'] == 'SOLOMON ISLANDS') | (paises['pais'] == 'VANUATU')]

pais  ataques
155  SOLOMON ISLANDS       29
191          VANUATU       14

In [8]:
#Dentre 'SOLOMON ISLANDS' e 'VANUATU', deixaremos o ataque como que pertencente à 'SOLOMON ISLANDS', pois possui mais ataques
#que 'VANUATU'

#Antes disso vamos apenas corrigir os países cujo problema é apenas a escrita e remover os '?'

dataset['pais'] = dataset['Country'].apply(lambda pais: 
                                           str(pais).upper().replace('?','').replace('BETWEEN ','').replace('PORTUGAL & ',
                                                                                                            'PORTUGAL / '))
dataset['pais'] = dataset['pais'].apply(lambda pais: str(pais).replace('UNITED ARAB EMIRATES (UAE)', 'UNITED ARAB EMIRATES'))
dataset['pais'] = dataset['pais'].apply(lambda pais: str(pais).replace('ST. MAARTIN', 'ST. MARTIN'))
dataset['pais'] = dataset['pais'].apply(lambda pais: str(pais).replace('ENGLAND', 'UNITED KINGDOM'))
#Vamos trocar Inglaterra por Reino Unido para não causar ambiguidade em uma futura visualização gráfica, já que a primeira faz
#parte do segundo

In [9]:
#Vamos criar uma função para definir o país com mais ataques em cada caso

def escolhe_pais(pais):
    if ' / ' in pais: #Executa a função caso o pais se enquadre nos casos avaliados
        paises_possiveis_list = str(pais).split(' / ') #Cria uma lista com os dois países possíveis

        paises_possiveis_dict = {}
        for pais in paises_possiveis_list:
            try:
                paises_possiveis_dict[pais] = paises['ataques'][pais] #Adiciona o país e seu nº de ataques ao dicinário criado
            except:
                paises_possiveis_dict[pais] = 0 #Adiciona o país e 0 ataques, caso não conste no dataframe países
        return max(paises_possiveis_dict,key=(lambda key: paises_possiveis_dict[key])) #Escolhe o país com o máximo de ataques
    else:
        return pais #Mantém o país igual caso não se enquadre nos casos avaliados

dataset['pais'] = list(map(escolhe_pais,dataset['pais']))

paises = dataset['pais'].value_counts().to_frame()
#Conta a ocorrência de cada país, converte em um dataframe, e organiza o index para melhor visualização
paises.rename(columns = {'pais':'ataques'}, inplace = True)
#Renomeia as colunas para termos mais adequados
paises

ataques
USA                         2160
AUSTRALIA                   1303
SOUTH AFRICA                 571
PAPUA NEW GUINEA             133
NEW ZEALAND                  126
...                          ...
PALESTINIAN TERRITORIES        1
BRITISH NEW GUINEA             1
NORTHERN ARABIAN SEA           1
TUVALU                         1
NETHERLANDS ANTILLES           1

[180 rows x 1 columns]

In [10]:
#Como podemos perceber, havia 16 locais ambíguos ou que precisavam de um tratamento prévio
#Podemos agora remover a coluna 'Country'
dataset.drop(columns = 'Country', inplace = True)

# Area

In [11]:
#Avaliando a coluna 'Area'
dataset['Area'].value_counts()

Florida              1015
New South Wales       476
Queensland            307
Hawaii                288
California            281
                     ... 
Mangaia Island          1
Corregidor Island       1
Washington              1
Sfax                    1
Central Tuamotu         1
Name: Area, Length: 799, dtype: int64

In [12]:
#Como são muitos casos e não foi seguida nenhuma padronização, vamos apenas padronizar a escrita com formato de primeiras
#letras maiúsculas. Além disso, demandaria muito tempo para pouco acréscimo de informação
dataset['Area'] = dataset['Area'].apply(lambda area: str(area).title())
dataset['Area'] = dataset['Area'].apply(lambda area: area.replace('Nan','Não informado'))

# Location

In [13]:
#Seguiremos a mesma lógica para a coluna 'Location'
dataset['Location'] = dataset['Location'].apply(lambda location: str(location).title())
dataset['Location'] = dataset['Location'].apply(lambda location: location.replace('Nan','Não informado'))

In [14]:
#Exporta o dataset resultante para csv, para registro e possibilita uso posterior
dataset.to_csv('C:/Users/m_hen/Favorites/dataset_shark_attacks_parte_2.csv',index = False)